## A workbook companion to the introduction to the DataFrames.jl package

*version: 2020-11-21* for DataFrames v0.22.1 and Julia v1.5.3

[Bogumił Kamiński](http://bogumilkaminski.pl/about/)

## Getting ready

We will use [this](http://archive.ics.uci.edu/ml/datasets/communities+and+crime) dataset. So first we download the required files.

In [1]:
using DataFrames
using CSV
using FreqTables
using Plots, StatsPlots
using GLM
using Statistics

You could also consider installing https://github.com/JuliaStats/StatsKit.jl package, but we want to be explicit what we use.

In [2]:
ENV["COLUMNS"] = 300
ENV["LINES"] = 20

20

## Loading the data

Here we have to do some non-standard operations.

In [3]:
colnamelines = filter(line -> startswith(line, "@attribute"), readlines("meta.txt"))

128-element Array{String,1}:
 "@attribute state numeric"
 "@attribute county numeric"
 "@attribute community numeric"
 "@attribute communityname string"
 "@attribute fold numeric"
 "@attribute population numeric"
 "@attribute householdsize numeric"
 "@attribute racepctblack numeric"
 ⋮
 "@attribute PolicCars numeric"
 "@attribute PolicOperBudg numeric"
 "@attribute LemasPctPolicOnPatr numeric"
 "@attribute LemasGangUnitDeploy numeric"
 "@attribute LemasPctOfficDrugUn numeric"
 "@attribute PolicBudgPerPop numeric"
 "@attribute ViolentCrimesPerPop numeric"

We need to convert column names to `Symbol` as this is the type that CSV.jl expects.

In [4]:
colnames = Symbol.(getindex.(split.(colnamelines), 2))

128-element Array{Symbol,1}:
 :state
 :county
 :community
 :communityname
 :fold
 :population
 :householdsize
 :racepctblack
 ⋮
 :PolicCars
 :PolicOperBudg
 :LemasPctPolicOnPatr
 :LemasGangUnitDeploy
 :LemasPctOfficDrugUn
 :PolicBudgPerPop
 :ViolentCrimesPerPop

In [5]:
coltypes = getindex.(split.(colnamelines), 3)

128-element Array{SubString{String},1}:
 "numeric"
 "numeric"
 "numeric"
 "string"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 ⋮
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"

In [6]:
df = CSV.File("data.txt", header=colnames) |> DataFrame

1994×128 DataFrame
  Row │ state  county  community  communityname        fold   population  householdsize  racepctblack  racePctWhite  racePctAsian  racePctHisp  agePct12t21  agePct12t29  agePct16t24  agePct65up  numbUrban  pctUrban  medIncome  pctWWage  pctWFarmSelf  pctWInvInc  pctWSocSec  pctWPubAsst  pctWRetire ⋯
      │ Int64  String  String     String               Int64  Float64     Float64        Float64       Float64       Float64       Float64      Float64      Float64      Float64      Float64     Float64    Float64   Float64    Float64   Float64       Float64     Float64     Float64      Float64    ⋯
──────┼─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
    1 │     8  ?       ?          Lakewoodcity             1        0.19           0.33          0.02          0.9           0.12         0.17         0.34         0.47         0.29        0.32       0.2       1.0        0.37      0.72          0.34        0.6         0.29         0.15        0.43 ⋯
    2 │    53  ?       ?          Tukwilacity              1        0.0            0.16          0.12          0.74          0.45         0.07         0.26         0.59         0.35        0.27       0.02      1.0        0.31      0.72          0.11        0.45        0.25         0.29        0.39
    3 │    24  ?       ?          Aberdeentown             1        0.0            0.42          0.49          0.56          0.17         0.04         0.39         0.47         0.28        0.32       0.0       0.0        0.3       0.58          0.19        0.39        0.38         0.4         0.84
    4 │    34  5       81440      Willingborotownship      1        0.04           0.77          1.0           0.08          0.12         0.1          0.51         0.5          0.34        0.21       0.06      1.0        0.58      0.89          0.21        0.43        0.36         0.2         0.82
    5 │    42  95      6096       Bethlehemtownship        1        0.01           0.55          0.02          0.95          0.09         0.05         0.38         0.38         0.23        0.36       0.02      0.9        0.5       0.72          0.16        0.68        0.44         0.11        0.71 ⋯
    6 │     6  ?       ?          SouthPasadenacity        1        0.02           0.28          0.06          0.54          1.0          0.25         0.31         0.48         0.27        0.37       0.04      1.0        0.52      0.68          0.2         0.61        0.28         0.15        0.25
  ⋮   │   ⋮      ⋮         ⋮               ⋮             ⋮        ⋮             ⋮             ⋮             ⋮             ⋮             ⋮            ⋮            ⋮            ⋮           ⋮           ⋮         ⋮          ⋮         ⋮           ⋮            ⋮           ⋮            ⋮           ⋮      ⋱
 1990 │    12  ?       ?          TempleTerracecity       10        0.01           0.4           0.1           0.87          0.12         0.16         0.43         0.51         0.35        0.3        0.03      1.0        0.42      0.74          0.14        0.64        0.3          0.06        0.46
 1991 │     6  ?       ?          Seasidecity             10        0.05           0.96          0.46          0.28          0.83         0.32         0.69         0.86         0.73        0.14       0.06      1.0        0.28      0.76          0.1         0.3         0.26         0.37        0.48
 1992 │     9  9       80070      Waterburytown           10        0.16           0.37          0.25          0.69          0.04         0.25         0.35         0.5          0.31        0.54       0.17      1.0        0.31      0.47          0.17        0.45        0.58         0.48        0.57 ⋯
 1993 │    25  17      72600      Walthamcity             10        0.08        

We see that theere is a problem that `?` indicates a missing value in the data set

In [7]:
df = CSV.File("data.txt", header=colnames, missingstring="?") |> DataFrame

1994×128 DataFrame
  Row │ state  county   community  communityname        fold   population  householdsize  racepctblack  racePctWhite  racePctAsian  racePctHisp  agePct12t21  agePct12t29  agePct16t24  agePct65up  numbUrban  pctUrban  medIncome  pctWWage  pctWFarmSelf  pctWInvInc  pctWSocSec  pctWPubAsst  pctWRetir ⋯
      │ Int64  Int64?   Int64?     String               Int64  Float64     Float64        Float64       Float64       Float64       Float64      Float64      Float64      Float64      Float64     Float64    Float64   Float64    Float64   Float64       Float64     Float64     Float64      Float64   ⋯
──────┼─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
    1 │     8  missing    missing  Lakewoodcity             1        0.19           0.33          0.02          0.9           0.12         0.17         0.34         0.47         0.29        0.32       0.2       1.0        0.37      0.72          0.34        0.6         0.29         0.15        0.4 ⋯
    2 │    53  missing    missing  Tukwilacity              1        0.0            0.16          0.12          0.74          0.45         0.07         0.26         0.59         0.35        0.27       0.02      1.0        0.31      0.72          0.11        0.45        0.25         0.29        0.3
    3 │    24  missing    missing  Aberdeentown             1        0.0            0.42          0.49          0.56          0.17         0.04         0.39         0.47         0.28        0.32       0.0       0.0        0.3       0.58          0.19        0.39        0.38         0.4         0.8
    4 │    34        5      81440  Willingborotownship      1        0.04           0.77          1.0           0.08          0.12         0.1          0.51         0.5          0.34        0.21       0.06      1.0        0.58      0.89          0.21        0.43        0.36         0.2         0.8
    5 │    42       95       6096  Bethlehemtownship        1        0.01           0.55          0.02          0.95          0.09         0.05         0.38         0.38         0.23        0.36       0.02      0.9        0.5       0.72          0.16        0.68        0.44         0.11        0.7 ⋯
    6 │     6  missing    missing  SouthPasadenacity        1        0.02           0.28          0.06          0.54          1.0          0.25         0.31         0.48         0.27        0.37       0.04      1.0        0.52      0.68          0.2         0.61        0.28         0.15        0.2
  ⋮   │   ⋮       ⋮         ⋮               ⋮             ⋮        ⋮             ⋮             ⋮             ⋮             ⋮             ⋮            ⋮            ⋮            ⋮           ⋮           ⋮         ⋮          ⋮         ⋮           ⋮            ⋮           ⋮            ⋮           ⋮     ⋱
 1990 │    12  missing    missing  TempleTerracecity       10        0.01           0.4           0.1           0.87          0.12         0.16         0.43         0.51         0.35        0.3        0.03      1.0        0.42      0.74          0.14        0.64        0.3          0.06        0.4
 1991 │     6  missing    missing  Seasidecity             10        0.05           0.96          0.46          0.28          0.83         0.32         0.69         0.86         0.73        0.14       0.06      1.0        0.28      0.76          0.1         0.3         0.26         0.37        0.4
 1992 │     9        9      80070  Waterburytown           10        0.16           0.37          0.25          0.69          0.04         0.25         0.35         0.5          0.31        0.54       0.17      1.0        0.31      0.47          0.17        0.45        0.58         0.48        0.5 ⋯
 1993 │    25       17      72600  Walthamcity             10        0.08       

Let us check if what we detected is consistent with the metadata

In [8]:
freqtable(eltype.(eachcol(df)), coltypes)

5×2 Named Array{Int64,2}
            Dim1 ╲ Dim2 │ "numeric"   "string"
────────────────────────┼─────────────────────
Int64                   │         2          0
Float64                 │       100          0
Union{Missing, Int64}   │         2          0
String                  │         0          1
Union{Missing, Float64} │        23          0

In [9]:
describe(df)

128×7 DataFrame
 Row │ variable             mean       min           median   max             nmissing  eltype                  
     │ Symbol               Union…     Any           Union…   Any             Int64     Type                    
─────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │ state                28.6836    1             34.0     56                     0  Int64
   2 │ county               58.8268    1             23.0     840                 1174  Union{Missing, Int64}
   3 │ community            46188.3    70            48090.0  94597               1177  Union{Missing, Int64}
   4 │ communityname                   Aberdeencity           Zanesvillecity         0  String
   5 │ fold                 5.49398    1             5.0      10                     0  Int64
   6 │ population           0.0575928  0.0           0.02     1.0                    0  Float64
  ⋮  │          ⋮               ⋮           ⋮           ⋮           ⋮            ⋮                 ⋮
 124 │ LemasPctPolicOnPatr  0.698589   0.0           0.75     1.0                 1675  Union{Missing, Float64}
 125 │ LemasGangUnitDeploy  0.440439   0.0           0.5      1.0                 1675  Union{Missing, Float64}
 126 │ LemasPctOfficDrugUn  0.0940522  0.0           0.0      1.0                    0  Float64
 127 │ PolicBudgPerPop      0.195078   0.0           0.15     1.0                 1675  Union{Missing, Float64}
 128 │ ViolentCrimesPerPop  0.237979   0.0           0.15     1.0                    0  Float64
                                                                                                117 rows omitted

## Analyzing the data

We will not want to use the first five columns from the data set. Let us get rid of them. This will be an in-place operation.

In [10]:
select!(df, Not(1:5))

1994×123 DataFrame
  Row │ population  householdsize  racepctblack  racePctWhite  racePctAsian  racePctHisp  agePct12t21  agePct12t29  agePct16t24  agePct65up  numbUrban  pctUrban  medIncome  pctWWage  pctWFarmSelf  pctWInvInc  pctWSocSec  pctWPubAsst  pctWRetire  medFamInc  perCapInc  whitePerCap  blackPerCap  indi ⋯
      │ Float64     Float64        Float64       Float64       Float64       Float64      Float64      Float64      Float64      Float64     Float64    Float64   Float64    Float64   Float64       Float64     Float64     Float64      Float64     Float64    Float64    Float64      Float64      Floa ⋯
──────┼─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
    1 │       0.19           0.33          0.02          0.9           0.12         0.17         0.34         0.47         0.29        0.32       0.2       1.0        0.37      0.72          0.34        0.6         0.29         0.15        0.43       0.39       0.4          0.39         0.32       ⋯
    2 │       0.0            0.16          0.12          0.74          0.45         0.07         0.26         0.59         0.35        0.27       0.02      1.0        0.31      0.72          0.11        0.45        0.25         0.29        0.39       0.29       0.37         0.38         0.33
    3 │       0.0            0.42          0.49          0.56          0.17         0.04         0.39         0.47         0.28        0.32       0.0       0.0        0.3       0.58          0.19        0.39        0.38         0.4         0.84       0.28       0.27         0.29         0.27
    4 │       0.04           0.77          1.0           0.08          0.12         0.1          0.51         0.5          0.34        0.21       0.06      1.0        0.58      0.89          0.21        0.43        0.36         0.2         0.82       0.51       0.36         0.4          0.39
    5 │       0.01           0.55          0.02          0.95          0.09         0.05         0.38         0.38         0.23        0.36       0.02      0.9        0.5       0.72          0.16        0.68        0.44         0.11        0.71       0.46       0.43         0.41         0.28       ⋯
    6 │       0.02           0.28          0.06          0.54          1.0          0.25         0.31         0.48         0.27        0.37       0.04      1.0        0.52      0.68          0.2         0.61        0.28         0.15        0.25       0.62       0.72         0.76         0.77
  ⋮   │     ⋮             ⋮             ⋮             ⋮             ⋮             ⋮            ⋮            ⋮            ⋮           ⋮           ⋮         ⋮          ⋮         ⋮           ⋮            ⋮           ⋮            ⋮           ⋮           ⋮          ⋮           ⋮            ⋮            ⋱
 1990 │       0.01           0.4           0.1           0.87          0.12         0.16         0.43         0.51         0.35        0.3        0.03      1.0        0.42      0.74          0.14        0.64        0.3          0.06        0.46       0.41       0.49         0.5          0.27
 1991 │       0.05           0.96          0.46          0.28          0.83         0.32         0.69         0.86         0.73        0.14       0.06      1.0        0.28      0.76          0.1         0.3         0.26         0.37        0.48       0.24       0.18         0.2          0.26
 1992 │       0.16           0.37          0.25          0.69          0.04         0.25         0.35         0.5          0.31        0.54       0.17      1.0        0.31      0.47          0.17        0.45        0.58         0.48        0.57       0.35       0.31         0.34         0.25       ⋯
 1993 │       0.08           0.51          0.06          0.87          0.22         0.1          0.58         0.74  

Analyzing the correlation between `:ViolentCrimesPerProp` and other variables.

The challenge is that some of the variables have missing data and other do not have them. We want to use pairwise complete observations approach (delete only what we have to delete when calculating the correlation).

This will be our fisrst encounter with views of a `DataFrame`. The use of `@view` avoids copying of the data. This improves the performance, but in general you should not mutate the view, as the changes will propagate back to the parent.

In [11]:
results = DataFrame()
for col in names(df, Not("ViolentCrimesPerPop"))
    cols = [col, "ViolentCrimesPerPop"]
    subdf = @view df[completecases(df, cols), cols]
    push!(results, (vairable=col, correlation=cor(subdf[!, 1], subdf[!, 2])))
end

In [12]:
results

122×2 DataFrame
 Row │ vairable             correlation 
     │ String               Float64     
─────┼──────────────────────────────────
   1 │ population             0.367157
   2 │ householdsize         -0.0349226
   3 │ racepctblack           0.631264
   4 │ racePctWhite          -0.68477
   5 │ racePctAsian           0.0376218
   6 │ racePctHisp            0.29305
  ⋮  │          ⋮                ⋮
 118 │ PolicOperBudg          0.33819
 119 │ LemasPctPolicOnPatr   -0.082317
 120 │ LemasGangUnitDeploy    0.116163
 121 │ LemasPctOfficDrugUn    0.348627
 122 │ PolicBudgPerPop        0.0959612
                        111 rows omitted

What if we want to see the most correlated values on top of the data frame?

In [13]:
sort!(results, :correlation, by = abs, rev=true)

122×2 DataFrame
 Row │ vairable               correlation 
     │ String                 Float64     
─────┼────────────────────────────────────
   1 │ PctKids2Par             -0.738424
   2 │ PctIlleg                 0.737957
   3 │ PctFam2Par              -0.706667
   4 │ racePctWhite            -0.68477
   5 │ PctYoungKids2Par        -0.666059
   6 │ PctTeen2Par             -0.661582
  ⋮  │           ⋮                 ⋮
 118 │ householdsize           -0.0349226
 119 │ PolicAveOTWorked         0.0336298
 120 │ PctWorkMomYoungKids     -0.0225354
 121 │ PctVacMore6Mos           0.0212828
 122 │ PctSameState85          -0.0194589
                          111 rows omitted

Now let us do some additional analyses.

In [14]:
@df select(df, [results[1:4, 1]; "ViolentCrimesPerPop"]) corrplot(cols(1:5))

In [15]:
lm(@formula(ViolentCrimesPerPop ~ PctKids2Par + PctIlleg + racePctWhite), df)

StatsModels.TableRegressionModel{LinearModel{GLM.LmResp{Array{Float64,1}},GLM.DensePredChol{Float64,LinearAlgebra.Cholesky{Float64,Array{Float64,2}}}},Array{Float64,2}}

ViolentCrimesPerPop ~ 1 + PctKids2Par + PctIlleg + racePctWhite

Coefficients:
───────────────────────────────────────────────────────────────────────────
                  Coef.  Std. Error       t  Pr(>|t|)  Lower 95%  Upper 95%
───────────────────────────────────────────────────────────────────────────
(Intercept)    0.649797   0.0343578   18.91    <1e-72   0.582416   0.717178
PctKids2Par   -0.444269   0.0322473  -13.78    <1e-40  -0.507511  -0.381027
PctIlleg       0.192406   0.0346147    5.56    <1e-7    0.124521   0.260291
racePctWhite  -0.244363   0.0225653  -10.83    <1e-25  -0.288617  -0.200108
───────────────────────────────────────────────────────────────────────────

Now feel free to experiment with the data set.